In [13]:
import pandas as pd 
import numpy as np

visa_experience = '/Users/churnika/Desktop/Projects/ML-Crate/F1 Visa Experiences/Dataset/telegram.csv'
visa_data = pd.read_csv(visa_experience) 

visa_data_clean = visa_data.dropna() #removing rows with missing values

visa_data_clean.describe(include='all')

msg_id                 date  \
count   6391.000000                 6391   
unique          NaN                 6372   
top             NaN  2021-07-01 04:30:10   
freq            NaN                    2   
mean    3384.868252                  NaN   
std     1908.469258                  NaN   
min        4.000000                  NaN   
25%     1768.500000                  NaN   
50%     3401.000000                  NaN   
75%     5034.500000                  NaN   
max     6715.000000                  NaN   

                                                  message  
count                                                6391  
unique                                               6317  
top     Look this out for visa alerts👇\nhttps://t.me/A...  
freq                                                    5  
mean                                                  NaN  
std                                                   NaN  
min                                                   NaN  
25%                                                   NaN  
50%                                                   NaN  
75%                                                   NaN  
max                                                   NaN

In [14]:
# accessing the message column and converting it into lower case

msg_exp = visa_data_clean['message'].str.lower()

In [15]:
print(msg_exp)

0       consulate: new delhi\nfirst attempt\nbiometric...
1       date: 24-03-2022\ndelhi consulate\ninterview t...
2       first attempt rejected in mumbai \ndelhi consu...
3       date 17 march 2022\nlocation- new delhi\ncount...
4       location mumbai\ndate 21 march\ncounter 33\nht...
                              ...                        
6438    consulate- mumbai\ndate-27th october\nappointm...
6439    consulate: hyderabad\ncounters open: 1\ncounte...
6440    location: mumbai\ndate : 23 oct 2020\napproved...
6441    kolkata counsulate \n8.0 am slot\ndate:19th oc...
6442    visa #experience\nuniversity: stonybrook unive...
Name: message, Length: 6391, dtype: object


In [16]:
# removing the urls that are present.

import re

text_without_urls = []

def remove_urls(text):
    url_pattern = re.compile(r'https?://\S+|www\.\S+')
    text_without_urls = url_pattern.sub('',text)
    return text_without_urls

for i in range(len(msg_exp)):
    try:
        msg_exp[i] = remove_urls(msg_exp[i])
        text_without_urls.append(msg_exp[i])
    except KeyError as e:
        # print(f"Error at index {i}: {e}. Skipping...")
        continue


In [17]:
# removing punctuations

import string

def remove_punctuation(text):
    translator = str.maketrans('', '', string.punctuation)
    return text.translate(translator)

print("Length of text_without_urls:", len(text_without_urls))

for i in range(len(text_without_urls)):
    try:
        text_without_urls[i] = remove_punctuation(text_without_urls[i])

    except KeyError as e:
        print(f"Error at index {i}: {e}. Skipping...")
        continue

Length of text_without_urls: 6340


In [18]:
# tokenisation

import spacy

# Load the English language model
nlp = spacy.load("en_core_web_sm")

# Tokenize text and remove URLs
cleaned_tokens = []

    
for i in range(len(text_without_urls)):
    try:
        doc = nlp(text_without_urls[i])
        # Extract tokens from the document and filter out URLs
        tokens = [token.text for token in doc if not token.like_url]
        cleaned_tokens.append(tokens)
    except Exception as e:
        print(f"Error at index {i}: {e}. Skipping...")
        continue

# cleaned_tokens now contains the tokens without URLs for each text


In [19]:
# print(len(cleaned_tokens))
# print(len(text_without_urls))
# print(cleaned_tokens)

In [20]:
# Iterate through each element in cleaned_tokens and remove numbers from each token
for i in range(len(cleaned_tokens)):
    cleaned_tokens[i] = ''.join(char for char in cleaned_tokens[i] if not char.isdigit())

# Join the tokens back into sentences or text
cleaned_text = [''.join(tokens) for tokens in cleaned_tokens]

# Now cleaned_text contains the tokenized text without numbers for each text


In [24]:
# removing stop words

import nltk
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize

nltk.download('punkt')
nltk.download('stopwords')

text = cleaned_text
stop_words = set(stopwords.words('english'))

# Tokenize the text
# word_tokens = word_tokenize(text)

# Filter out the stopwords
filtered_tokens = [word for word in text if word.lower() not in stop_words]

[nltk_data] Downloading package punkt to /Users/churnika/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to
[nltk_data]     /Users/churnika/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [26]:
# print(filtered_tokens)

In [32]:
cleaned_exp = ' '.join(filtered_tokens)  # Join the words into a string
cleaned_exp = re.findall(r'\b\w+\b', cleaned_exp)  # Find all words in the string
print(cleaned_exp)


['consulatenewdelhi', 'firstattempt', 'biometricmarch10', 'interview', 'march11930am', 'intime9am', 'duration1tomin', 'statusapproved', 'universityauburnuniversityatmontgomery', 'vigoodmorning', 'megoodmorningsirhowareyousir', 'vifinethankyouforaskingpleasepassyourpassportandi20', 'meidid', 'visomastersinwhichcourse', 'mecomputersciencesir', 'vidoyouhavecomputersciencebackground', 'meyessirihaveyearsofexperienceasasoftwareengineer', 'vithenwhyyouwanttogonow', 'mesirihaveanexperienceasawebdevelopernowiwanttolearnbackendtechnologiestoupgrademyself', 'viwhattechnologiesspecifyit', 'mepythonsqldatabase', 'vihowthesearehelpfulforyou', 'meifilearnthosetechnologiesiwillbecomeafullstackdevelopersir', 'viwhatisyourbtechpercentage', 'meitswithfirstclasswithoutanybacklogsir', 'viwithoutanybacklogs', 'meyessir', 'viiamapprovingyourvisa', 'methankyousomuchsiryoumademyday', 'psitoogottensedalotbuttheyareveryfriendlywithussojustbeconfident', 'finallythankyouforthisgroupandthosewhosharethereexperience

In [35]:
print(len(cleaned_exp))
print(cleaned_exp[100])


248471
am


In [39]:
# Stemmer and Lemmatizer

from nltk.stem import PorterStemmer, WordNetLemmatizer

nltk.download('wordnet')

# Initialize stemmer and lemmatizer
stemmer = PorterStemmer()
lemmatizer = WordNetLemmatizer()

stem_lem = []

# Example word
for i in range(len(cleaned_exp)):
    word = cleaned_exp[i]
    stemmed_word = stemmer.stem(word)
    lemmatized_word = lemmatizer.lemmatize(word)
    if(stemmed_word == lemmatized_word):
        stem_lem.append(stemmed_word)
    else:
        stem_lem.append(stemmed_word)
        stem_lem.append(lemmatized_word)

[nltk_data] Downloading package wordnet to
[nltk_data]     /Users/churnika/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


In [48]:
# removing special characters

cleaned_exp = []

for i in range(len(stem_lem)):
    stem_lem[i] = re.sub(r'[^\w\s]', '', stem_lem[i])
